In [1]:
import requests
import json
import pandas as pd
from pandas import json_normalize
import config
from db_manager import DBManager
import os
from rest_api import Api
from datetime import date
from dateutil.relativedelta import relativedelta
from urllib.parse import quote_plus
from sqlalchemy import create_engine
import itertools
import logging

In [2]:
logging.basicConfig(
    format='%(levelname)s-%(name)s:%(lineno)s-%(message)s',
    datefmt='%Y-%m-%d %H:%M:%S',
    level='INFO'
)
logger=logging.getLogger(__name__)

#### Show all columns without truncating

In [3]:
pd.set_option('display.max_columns', None)

Today's date

In [4]:
today = date.today()
print(today)

2023-08-23


Adding months to today's date. Near term travel dates 30 - 60 days ahead

In [5]:
departure_date_1_month = today + relativedelta(months=1)
departure_date_2_month = today + relativedelta(months=2)
return_date_1_month = departure_date_2_month
return_date_2_month = today + relativedelta(months=3)
print(f'Departure_dates:{departure_date_1_month} and {departure_date_2_month} \nReturn dates:{return_date_1_month} and {return_date_2_month}')

Departure_dates:2023-09-23 and 2023-10-23 
Return dates:2023-10-23 and 2023-11-23


Get the nearby festival departure dates by start_date from the public.indian_holidays table

In [11]:
# credentials=config.pg_credentials
# db = DBManager(credentials=credentials)
# df_departure_arrival_dates = db.run_query(query_file_name='festival_dates')

In [12]:
#df_departure_arrival_dates 

Apply the combination of params to get data for all possible combinations of depart, arrival dates and depart arrival airports

Combination itertools usage. Im calculating the total combinations by multiplying the number of possibilities (unique values) for each variable<br />
Departure airport: 4 possibilities<br />
Arrival airport: 6 possibilities<br />
Departure date: 1 possibilities<br />
Arrival date: 1 possibilities<br />
Total combinations = 4 x 6 x 1 x 1 = 24 combinations

#### Travel payouts API to get flight search results for each combination in the list 

--------------------------------------------------------

API test for amadeus

POST request to the Amadeus authorization server to get the access token

In [6]:
response = requests.post(url=config.url_token, headers=config.headers_token, data=config.data)

if response.status_code == 200:
  # API call succeeded
  token = response.json()['access_token'] 
  logger.info('Successful access token generation')
else:
  # API call failed
  print(response.text)

INFO-__main__:6-Successful access token generation


In [7]:
#Combinations of destination and origin airport codes
origins = config.params['originLocationCode']
destinations = config.params['destinationLocationCode']
departure_dates=[departure_date_1_month,departure_date_2_month]
return_dates=[return_date_1_month,return_date_2_month]

Creating combinations of Origin and Destination to be passed as parameters to the api call

In [10]:
#api headers
headers = {
  'client_id': config.client_id, 
  'client_secret': config.client_secret,
  'Authorization': f'Bearer {token}' 
}

#create a list
response = []
#combo of dates
date_combos = list(itertools.product(departure_dates, return_dates))

for origin, dest, (depart, ret) in itertools.product(origins, destinations, date_combos):
  
  params={
    'originLocationCode': origin,
    'destinationLocationCode':dest, 
    'departureDate': depart, 
    'returnDate' : ret,
    'adults':1,
    'children':None,
    'infants':None,
    'travelClass':None,
    'currencyCode':'EUR',
    'maxPrice' : None
    }
#api call
  api = Api()
  resp = api.make_flight_api_request(url=config.url,headers=headers,params=params)
  response.append(resp)
logger.info('API successful call')
print(response)

Error making API request: 401 - 
            {
                "errors": [
                        {
                            "code": 38191,
                            "title": "Invalid HTTP header",
                            "detail": "Missing or invalid format for mandatory Authorization header",
                            "status": 401
                        }
                ]
            }
        
Error making API request: 401 - 
            {
                "errors": [
                        {
                            "code": 38191,
                            "title": "Invalid HTTP header",
                            "detail": "Missing or invalid format for mandatory Authorization header",
                            "status": 401
                        }
                ]
            }
        
Error making API request: 401 - 
            {
                "errors": [
                        {
                            "code": 38191,
                          

INFO-__main__:31-API successful call


Error making API request: 401 - 
            {
                "errors": [
                        {
                            "code": 38191,
                            "title": "Invalid HTTP header",
                            "detail": "Missing or invalid format for mandatory Authorization header",
                            "status": 401
                        }
                ]
            }
        
Error making API request: 401 - 
            {
                "errors": [
                        {
                            "code": 38191,
                            "title": "Invalid HTTP header",
                            "detail": "Missing or invalid format for mandatory Authorization header",
                            "status": 401
                        }
                ]
            }
        


AttributeError: 'list' object has no attribute 'head'

In [67]:
data['data'][0]

{'type': 'flight-offer',
 'id': '1',
 'source': 'GDS',
 'instantTicketingRequired': False,
 'nonHomogeneous': False,
 'oneWay': False,
 'lastTicketingDate': '2023-08-25',
 'lastTicketingDateTime': '2023-08-25',
 'numberOfBookableSeats': 9,
 'itineraries': [{'duration': 'PT13H15M',
   'segments': [{'departure': {'iataCode': 'FRA',
      'terminal': '2',
      'at': '2023-11-01T21:00:00'},
     'arrival': {'iataCode': 'AUH',
      'terminal': '3',
      'at': '2023-11-02T06:00:00'},
     'carrierCode': 'EY',
     'number': '8',
     'aircraft': {'code': '789'},
     'operating': {'carrierCode': 'EY'},
     'duration': 'PT6H',
     'id': '96',
     'numberOfStops': 0,
     'blacklistedInEU': False},
    {'departure': {'iataCode': 'AUH',
      'terminal': '3',
      'at': '2023-11-02T09:55:00'},
     'arrival': {'iataCode': 'DEL',
      'terminal': '3',
      'at': '2023-11-02T14:45:00'},
     'carrierCode': 'EY',
     'number': '210',
     'aircraft': {'code': '32A'},
     'operating': {'

Convert that sample nested JSON data into separate DataFrames

In [105]:
# Flight offers DataFrame
offers_df = pd.DataFrame(data['data'])

# Itineraries DataFrame
itineraries_df = pd.json_normalize(data['data'], record_path='itineraries', meta=['id', 'source'])

# Traveler pricing DataFrame
traveler_pricing_df = pd.json_normalize(data['data'], record_path=['travelerPricings'], meta=['id', 'source'])


In [114]:
# Extract out the fare details array
offers_df.head()

type id source  instantTicketingRequired  nonHomogeneous  oneWay  \
0  flight-offer  1    GDS                     False           False   False   
1  flight-offer  2    GDS                     False           False   False   
2  flight-offer  3    GDS                     False           False   False   
3  flight-offer  4    GDS                     False           False   False   
4  flight-offer  5    GDS                     False           False   False   

  lastTicketingDate lastTicketingDateTime  numberOfBookableSeats  \
0        2023-08-25            2023-08-25                      9   
1        2023-08-25            2023-08-25                      9   
2        2023-08-25            2023-08-25                      9   
3        2023-08-25            2023-08-25                      9   
4        2023-11-01            2023-11-01                      9   

                                         itineraries  \
0  [{'duration': 'PT13H15M', 'segments': [{'depar...   
1  [{'duration': 'PT17H50M', 'segments': [{'depar...   
2  [{'duration': 'PT25H30M', 'segments': [{'depar...   
3  [{'duration': 'PT30H5M', 'segments': [{'depart...   
4  [{'duration': 'PT21H', 'segments': [{'departur...   

                                               price  \
0  {'currency': 'EUR', 'total': '359.58', 'base':...   
1  {'currency': 'EUR', 'total': '359.58', 'base':...   
2  {'currency': 'EUR', 'total': '359.58', 'base':...   
3  {'currency': 'EUR', 'total': '359.58', 'base':...   
4  {'currency': 'EUR', 'total': '400.99', 'base':...   

                                      pricingOptions validatingAirlineCodes  \
0  {'fareType': ['PUBLISHED'], 'includedCheckedBa...                   [EY]   
1  {'fareType': ['PUBLISHED'], 'includedCheckedBa...                   [EY]   
2  {'fareType': ['PUBLISHED'], 'includedCheckedBa...                   [EY]   
3  {'fareType': ['PUBLISHED'], 'includedCheckedBa...                   [EY]   
4  {'fareType': ['PUBLISHED'], 'includedCheckedBa...                   [SV]   

                                    travelerPricings  
0  [{'travelerId': '1', 'fareOption': 'STANDARD',...  
1  [{'travelerId': '1', 'fareOption': 'STANDARD',...  
2  [{'travelerId': '1', 'fareOption': 'STANDARD',...  
3  [{'travelerId': '1', 'fareOption': 'STANDARD',...  
4  [{'travelerId': '1', 'fareOption': 'STANDARD',...

In [111]:
fair_details

[[{'travelerId': '1',
   'fareOption': 'STANDARD',
   'travelerType': 'ADULT',
   'price': {'currency': 'EUR', 'total': '359.58', 'base': '135.00'},
   'fareDetailsBySegment': [{'segmentId': '96',
     'cabin': 'ECONOMY',
     'fareBasis': 'ULN10V2F',
     'brandedFare': 'YV',
     'class': 'U',
     'includedCheckedBags': {'weight': 30, 'weightUnit': 'KG'}},
    {'segmentId': '97',
     'cabin': 'ECONOMY',
     'fareBasis': 'ULN10V2F',
     'brandedFare': 'YV',
     'class': 'U',
     'includedCheckedBags': {'weight': 30, 'weightUnit': 'KG'}}]}],
 [{'travelerId': '1',
   'fareOption': 'STANDARD',
   'travelerType': 'ADULT',
   'price': {'currency': 'EUR', 'total': '359.58', 'base': '135.00'},
   'fareDetailsBySegment': [{'segmentId': '221',
     'cabin': 'ECONOMY',
     'fareBasis': 'ULN10V2F',
     'brandedFare': 'YV',
     'class': 'U',
     'includedCheckedBags': {'weight': 30, 'weightUnit': 'KG'}},
    {'segmentId': '222',
     'cabin': 'ECONOMY',
     'fareBasis': 'ULN10V2F',
   

In [100]:
traveler_pricing_df.head()

travelerId fareOption travelerType fareDetailsBySegment price.currency  \
0          1   STANDARD        ADULT            segmentId            EUR   
0          1   STANDARD        ADULT                cabin            EUR   
0          1   STANDARD        ADULT            fareBasis            EUR   
0          1   STANDARD        ADULT          brandedFare            EUR   
0          1   STANDARD        ADULT                class            EUR   

  price.total price.base id source  
0      359.58     135.00  1    GDS  
0      359.58     135.00  1    GDS  
0      359.58     135.00  1    GDS  
0      359.58     135.00  1    GDS  
0      359.58     135.00  1    GDS

In [99]:
# Explode list to rows

traveler_pricing_df = traveler_pricing_df.explode('fareDetailsBySegment')

In [94]:
traveler_pricing_df = traveler_pricing_df.pivot(index='id', columns='fareDetailsBySegment', values='b').reset_index()


KeyError: 'a'

Dropping unwanted columns from the above respective tables

In [86]:
# prices_df=prices_df.drop(columns=['fees','additionalServices'])
# offers_df=offers_df.drop(columns=['itineraries','price','pricingOptions','travelerPricings'])
offers_df

To split a column containing a list of dictionaries into multiple columns in a DataFrame, avoiding duplication, you can:

Explode the list column to rows
Pivot the exploded rows into columns

---------------------------------------------------

#### df_legs is the main table that contains leg id, dep time, arr time, dep airport, arr airport, stopovers, duration </br> Looping through the response

In [57]:
legs=[]
response = [r for r in response if r is not None]
for i in response:
    if 'legs' in i:
        dict = i['legs']
        legs.append(dict)
    else:
        legs = None
print(legs)

[[{'id': 'BER-DEL:AF1835~19:AF226~20:0', 'departureTime': '18:10', 'arrivalTime': '22:35', 'duration': '24h 55m', 'departureAirportCode': 'BER', 'arrivalAirportCode': 'DEL', 'airlineCodes': ['AF'], 'stopoverAirportCodes': ['CDG'], 'allianceCodes': ['sky_team'], 'stopoversCount': 1, 'departureTimeMinutes': 1090, 'arrivalTimeMinutes': 1355, 'departureDateTime': '2023-09-19T18:10:00.000+02:00', 'arrivalDateTime': '2023-09-20T22:35:00.000+05:30', 'stopoverDurationMinutes': 860, 'durationMinutes': 1495, 'overnight': True, 'stopoverDuration': '14h 20m', 'durationDays': 1, 'longStopover': True, 'segments': [{'durationMinutes': 110, 'stopoverDurationMinutes': 860, 'departureAirportCode': 'BER', 'arrivalAirportCode': 'CDG', 'airlineCode': 'AF', 'operatingAirlineCode': 'A5', 'cabin': 'economy', 'designatorCode': 'AF1835', 'departureDateTime': '2023-09-19T18:10:00.000+02:00', 'arrivalDateTime': '2023-09-19T20:00:00.000+02:00'}, {'durationMinutes': 525, 'stopoverDurationMinutes': 0, 'departureAirp

In [58]:
new_df_legs=pd.DataFrame()
for l in legs:
  df=json_normalize(l)
  new_df_legs=new_df_legs.append(df)
print(new_df_legs)

  

                                        id departureTime arrivalTime duration  \
0             BER-DEL:AF1835~19:AF226~20:0         18:10       22:35  24h 55m   
1             BER-DEL:KL1822~19:KL871~19:0         09:05       01:55  13h 20m   
2             DEL-BER:KL872~19:KL1829~19:1         03:55       16:40  16h 15m   
3             DEL-BER:KL872~19:KL1833~19:1         03:55       20:05  19h 40m   
4             DEL-BER:AF225~19:AF1134~19:1         00:35       22:40  25h 35m   
..                                     ...           ...         ...      ...   
17  MAA-BER:AF6458~19:AF191~20:AF1234~20:1         23:15       14:50  20h 05m   
18  MAA-BER:AF3770~19:AF225~20:AF1734~20:1         18:30       11:30  21h 30m   
19  BER-MAA:KL1822~19:KL877~19:KL3688~20:0         09:05       08:55  20h 20m   
20            BER-MAA:AF1835~19:AF108~20:0         18:10       23:30  25h 50m   
21            BER-MAA:AF1235~19:AF108~20:0         15:20       23:30  28h 40m   

   departureAirportCode arr

In [59]:
#new_df_legs.shape

(456, 30)

In [61]:
#new_df_legs.departureAirportCode.unique()

array(['BER', 'DEL', 'BOM', 'BLR', 'HYD', 'MAA'], dtype=object)

Dropping unwanted columns

In [62]:
new_df_legs=new_df_legs.drop(columns=['departureTimeMinutes','arrivalTimeMinutes','segments','operatingAirlineCodes','stopoverCode','shortStopover','earlyDeparture','lateArrival','newAircraft','oldAircraft','highlyRatedCarrier','score'])

In [89]:
new_df_legs['incremental_day']=today

In [90]:
new_df_legs.head()

id departureTime arrivalTime duration  \
0  BER-DEL:AF1835~19:AF226~20:0         18:10       22:35  24h 55m   
1  BER-DEL:KL1822~19:KL871~19:0         09:05       01:55  13h 20m   
2  DEL-BER:KL872~19:KL1829~19:1         03:55       16:40  16h 15m   
3  DEL-BER:KL872~19:KL1833~19:1         03:55       20:05  19h 40m   
4  DEL-BER:AF225~19:AF1134~19:1         00:35       22:40  25h 35m   

  departureAirportCode arrivalAirportCode airlineCodes stopoverAirportCodes  \
0                  BER                DEL         [AF]                [CDG]   
1                  BER                DEL         [KL]                [AMS]   
2                  DEL                BER         [KL]                [AMS]   
3                  DEL                BER         [KL]                [AMS]   
4                  DEL                BER         [AF]                [CDG]   

  allianceCodes  stopoversCount              departureDateTime  \
0    [sky_team]               1  2023-09-19T18:10:00.000+02:00   
1    [sky_team]               1  2023-09-19T09:05:00.000+02:00   
2    [sky_team]               1  2023-10-19T03:55:00.000+05:30   
3    [sky_team]               1  2023-10-19T03:55:00.000+05:30   
4    [sky_team]               1  2023-10-19T00:35:00.000+05:30   

                 arrivalDateTime  stopoverDurationMinutes  durationMinutes  \
0  2023-09-20T22:35:00.000+05:30                      860             1495   
1  2023-09-20T01:55:00.000+05:30                      215              800   
2  2023-10-19T16:40:00.000+02:00                      320              975   
3  2023-10-19T20:05:00.000+02:00                      530             1180   
4  2023-10-19T22:40:00.000+02:00                      840             1535   

   overnight stopoverDuration  durationDays  longStopover incremental_day  
0       True          14h 20m             1          True      2023-08-19  
1       True          03h 35m             1         False      2023-08-19  
2      False          05h 20m             0          True      2023-08-19  
3      False          08h 50m             0          True      2023-08-19  
4      False              14h             0          True      2023-08-19

#### df_trips is the df that acts as an intermediate df between legs and fares array. It contains the trip id and the legs id

Creating a list of dicts for trips from the resposnse and removing None

In [70]:
trips=[]
response = [r for r in response if r is not None]
for i in response:
    if 'trips' in i:
        dict = i['trips']
        trips.append(dict)
    else:
        trips = None
print(trips)

[[{'id': '67edb3a644428b4emsr:AF1535~19-AF226~20=AF225~19-AF1534~19', 'code': 'AF1535~19-AF226~20=AF225~19-AF1534~19', 'legIds': ['BER-DEL:AF1535~19:AF226~20:0', 'DEL-BER:AF225~19:AF1534~19:1']}, {'id': '67edb3a644428b4emsr:AF1135~19-AF226~19=AF225~19-AF1834~19', 'code': 'AF1135~19-AF226~19=AF225~19-AF1834~19', 'legIds': ['BER-DEL:AF1135~19:AF226~19:0', 'DEL-BER:AF225~19:AF1834~19:1']}, {'id': '67edb3a644428b4emsr:KL1822~19-KL871~19=AF225~19-AF1734~19', 'code': 'KL1822~19-KL871~19=AF225~19-AF1734~19', 'legIds': ['BER-DEL:KL1822~19:KL871~19:0', 'DEL-BER:AF225~19:AF1734~19:1']}, {'id': '67edb3a644428b4emsr:AF1835~19-AF226~20=AF225~19-AF1534~19', 'code': 'AF1835~19-AF226~20=AF225~19-AF1534~19', 'legIds': ['BER-DEL:AF1835~19:AF226~20:0', 'DEL-BER:AF225~19:AF1534~19:1']}, {'id': '67edb3a644428b4emsr:KL1834~19-KL871~20=KL872~19-KL1831~19', 'code': 'KL1834~19-KL871~20=KL872~19-KL1831~19', 'legIds': ['BER-DEL:KL1834~19:KL871~20:0', 'DEL-BER:KL872~19:KL1831~19:1']}, {'id': '67edb3a644428b4emsr:

looping through the trips list

In [71]:
new_df_trips=pd.DataFrame()
for t in trips:
  df=json_normalize(t)
  new_df_trips=new_df_trips.append(df)
print(new_df_trips)

                                                   id  \
0   67edb3a644428b4emsr:AF1535~19-AF226~20=AF225~1...   
1   67edb3a644428b4emsr:AF1135~19-AF226~19=AF225~1...   
2   67edb3a644428b4emsr:KL1822~19-KL871~19=AF225~1...   
3   67edb3a644428b4emsr:AF1835~19-AF226~20=AF225~1...   
4   67edb3a644428b4emsr:KL1834~19-KL871~20=KL872~1...   
..                                                ...   
80  5c8c50c973fd45a5msr:AF1835~19-AF108~20=AF115~1...   
81  5c8c50c973fd45a5msr:AF1135~19-AF212~19-AF3326~...   
82  5c8c50c973fd45a5msr:KL1820~19-KL871~19-KL3664~...   
83  5c8c50c973fd45a5msr:AF1135~19-AF212~19-AF3326~...   
84  5c8c50c973fd45a5msr:KL1822~19-KL877~19-KL3688~...   

                                                 code  \
0               AF1535~19-AF226~20=AF225~19-AF1534~19   
1               AF1135~19-AF226~19=AF225~19-AF1834~19   
2               KL1822~19-KL871~19=AF225~19-AF1734~19   
3               AF1835~19-AF226~20=AF225~19-AF1534~19   
4               KL1834~19-KL87

Exploding the legIds column to spread the list of ledIds to several rows

In [81]:
new_df_trips=new_df_trips.explode('legIds')

In [91]:
new_df_trips['incremental_day']=today

In [92]:
new_df_trips.head()

id  \
0  67edb3a644428b4emsr:AF1535~19-AF226~20=AF225~1...   
0  67edb3a644428b4emsr:AF1535~19-AF226~20=AF225~1...   
1  67edb3a644428b4emsr:AF1135~19-AF226~19=AF225~1...   
1  67edb3a644428b4emsr:AF1135~19-AF226~19=AF225~1...   
2  67edb3a644428b4emsr:KL1822~19-KL871~19=AF225~1...   

                                    code                        legIds  \
0  AF1535~19-AF226~20=AF225~19-AF1534~19  BER-DEL:AF1535~19:AF226~20:0   
0  AF1535~19-AF226~20=AF225~19-AF1534~19  DEL-BER:AF225~19:AF1534~19:1   
1  AF1135~19-AF226~19=AF225~19-AF1834~19  BER-DEL:AF1135~19:AF226~19:0   
1  AF1135~19-AF226~19=AF225~19-AF1834~19  DEL-BER:AF225~19:AF1834~19:1   
2  KL1822~19-KL871~19=AF225~19-AF1734~19  BER-DEL:KL1822~19:KL871~19:0   

  incremental_day  
0      2023-08-19  
0      2023-08-19  
1      2023-08-19  
1      2023-08-19  
2      2023-08-19

#### df_fares is where we have the price and currency info for the trips seen in legs array. Here you have columhns such as tripId, currencyCode and totalAmount

In [109]:
fares=[]
response = [r for r in response if r is not None]
for i in response:
    if 'fares' in i:
        dict = i['fares']
        fares.append(dict)
    else:
        fares = None
print(fares)

[[{'paymentFees': [{'paymentMethodId': 10, 'currencyCode': 'EUR', 'amount': 0, 'amountUsd': 0, 'totalAmount': 0, 'totalAmountUsd': 0}, {'paymentMethodId': 15, 'currencyCode': 'EUR', 'amount': 0, 'amountUsd': 0, 'totalAmount': 0, 'totalAmountUsd': 0}], 'id': '67edb3a644428b4emsr:klm.com:ce9909b9d30d0889', 'price': {'totalAmount': 529, 'totalAmountUsd': 576.0435, 'amount': 529, 'amountUsd': 576.0435, 'originalAmount': 528.99, 'originalAmountUsd': 576.0435, 'amountPerAdult': 528.99, 'amountPerChild': 0, 'amountPerInfant': 0, 'taxAmount': 0, 'taxAmountUsd': 0, 'totalTaxAmount': 0, 'totalTaxAmountUsd': 0, 'currencyCode': 'EUR', 'paymentFeeAmountUsd': 0, 'bookingFee': 0, 'bookingFeeUsd': 0, 'totalBookingFee': 0, 'totalBookingFeeUsd': 0}, 'providerCode': 'klm.com', 'handoffUrl': 'https://handoff.wego.com/flights/continue?currency=EUR&url_locale=en&site_code=US&device_type=desktop&app_type=WEB_APP&domain=www.wego.com&fare_id=67edb3a644428b4emsr:klm.com:ce9909b9d30d0889&route=BER-DEL&search_id=

In [110]:
new_df_fares=pd.DataFrame()
for t in fares:
  df=json_normalize(t)
  new_df_fares=new_df_fares.append(df)
print(new_df_fares)

                                          paymentFees  \
0   [{'paymentMethodId': 10, 'currencyCode': 'EUR'...   
1   [{'paymentMethodId': 10, 'currencyCode': 'EUR'...   
2   [{'paymentMethodId': 10, 'currencyCode': 'EUR'...   
3   [{'paymentMethodId': 10, 'currencyCode': 'EUR'...   
4   [{'paymentMethodId': 10, 'currencyCode': 'EUR'...   
..                                                ...   
80  [{'paymentMethodId': 3, 'currencyCode': 'EUR',...   
81  [{'paymentMethodId': 3, 'currencyCode': 'EUR',...   
82  [{'paymentMethodId': 3, 'currencyCode': 'EUR',...   
83  [{'paymentMethodId': 3, 'currencyCode': 'EUR',...   
84  [{'paymentMethodId': 3, 'currencyCode': 'EUR',...   

                                                   id   providerCode  \
0        67edb3a644428b4emsr:klm.com:ce9909b9d30d0889        klm.com   
1        67edb3a644428b4emsr:klm.com:b50d58daca6a8025        klm.com   
2        67edb3a644428b4emsr:klm.com:480a4e3621bd342d        klm.com   
3        67edb3a644428b4ems

Rename columns that follows a certain pattern

In [111]:
new_df_fares.columns = new_df_fares.columns.str.replace("^price.", "", regex=True)


In [112]:
new_df_fares=new_df_fares.drop(columns=['paymentFees','handoffUrl','conditionIds','ecpc','legConditionIds','score','tags'])

In [113]:
new_df_fares['incremental_day']=today

In [114]:
new_df_fares.head()

id providerCode  \
0  67edb3a644428b4emsr:klm.com:ce9909b9d30d0889      klm.com   
1  67edb3a644428b4emsr:klm.com:b50d58daca6a8025      klm.com   
2  67edb3a644428b4emsr:klm.com:480a4e3621bd342d      klm.com   
3  67edb3a644428b4emsr:klm.com:cdf014a76dcb054a      klm.com   
4  67edb3a644428b4emsr:klm.com:c4acfb9b7ece91bf      klm.com   

   remainingSeatsCount  refundable  exchangeable  \
0                    0       False         False   
1                    0       False         False   
2                    0       False         False   
3                    0       False         False   
4                    0       False         False   

                                              tripId  totalAmount  \
0  67edb3a644428b4emsr:AF1535~19-AF226~20=AF225~1...          529   
1  67edb3a644428b4emsr:AF1535~19-AF226~20=AF225~1...          529   
2  67edb3a644428b4emsr:AF1535~19-AF226~20=AF225~1...          529   
3  67edb3a644428b4emsr:AF1535~19-AF226~20=AF225~1...          529   
4  67edb3a644428b4emsr:KL1834~19-KL871~20=AF225~1...          529   

   totalAmountUsd  amount  amountUsd  originalAmount  originalAmountUsd  \
0       576.04350     529  576.04350          528.99          576.04350   
1       576.04350     529  576.04350          528.99          576.04350   
2       576.04350     529  576.04350          528.99          576.04350   
3       576.04350     529  576.04350          528.99          576.04350   
4       576.29395     529  576.29395          529.22          576.29395   

   amountPerAdult  amountPerChild  amountPerInfant  taxAmount  taxAmountUsd  \
0          528.99               0                0        0.0           0.0   
1          528.99               0                0        0.0           0.0   
2          528.99               0                0        0.0           0.0   
3          528.99               0                0        0.0           0.0   
4          529.22               0                0        0.0           0.0   

   totalTaxAmount  totalTaxAmountUsd currencyCode  paymentFeeAmountUsd  \
0             0.0                0.0          EUR                    0   
1             0.0                0.0          EUR                    0   
2             0.0                0.0          EUR                    0   
3             0.0                0.0          EUR                    0   
4             0.0                0.0          EUR                    0   

   bookingFee  bookingFeeUsd  totalBookingFee  totalBookingFeeUsd  \
0           0              0                0                   0   
1           0              0                0                   0   
2           0              0                0                   0   
3           0              0                0                   0   
4           0              0                0                   0   

  incremental_day  
0      2023-08-19  
1      2023-08-19  
2      2023-08-19  
3      2023-08-19  
4      2023-08-19

Establish connection With postgresql DB. Note to use config file for storing passwords separately from the python code

In [115]:
credentials=config.pg_credentials
db = DBManager(credentials=credentials)
db.create_table_from_df(df=new_df_fares,table_name='fares')

INFO-db_manager:30-Keerthana%40123
INFO-db_manager:32-CONNECTED
INFO-db_manager:67-Dumped to DB
